In [1]:
import tensorflow as tf
from konlpy.tag import Twitter
import numpy as np
import gensim
import time

In [2]:
def read_data(filename):    
    with open(filename, 'r',encoding='utf-8') as f:
        data = [line.split('\t') for line in f.read().splitlines()]        
        data = data[1:]   # header 제외 #    
    return data 
    
train_data = read_data('data/ratings_train.txt')
# test_data = read_data('data/ratings_test.txt')
len(train_data)

150000

In [3]:
twitter = Twitter() 

def tokenize(doc):

    return ['/'.join(t) for t in twitter.pos(doc, norm=True, stem=True)]

# tokens = [tokenize(row[1]) for row in train_data]

In [4]:
# model = gensim.models.Word2Vec(size=300, sg=1, alpha=0.025, min_alpha=0.025, seed=410)
# model.build_vocab(tokens)
# model.train(tokens, model.corpus_count, epochs=model.epochs)

In [5]:
# '외계인/Noun' in model.wv.vocab

In [6]:
# model.save('word2vec.model')

In [7]:
model = gensim.models.word2vec.Word2Vec.load('word2vec.model')

In [8]:
# len(model.wv.vocab)

# def convert2Vec(model, doc):  ## Convert corpus into vectors
#     word_vec = []
#     word_num = 0
#     unk_num = 0
# #     print('doc : ', doc)
#     for sent in doc:
# #         print('sent : ', sent)
#         sub = []
#         for word in sent:
#             word_num += 1
#             if(word in model.wv.vocab):
# #                 print('word in sent')
#                 sub.append(model.wv[word])
#             else:
#                 unk_num += 1
# #                 print('word not in sent')
#                 sub.append(np.zeros(300)) ## used for OOV words
#         word_vec.append(sub)
#     print('word_num :', word_num, 'unk_num :', unk_num)
#     return word_vec

In [9]:
len(model.wv.vocab)

def convert2Vec(model, sent):  ## Convert corpus into vectors
    word_vec = []
#     print(sent)
    for word in sent:
        if(word in model.wv.vocab):
            word_vec.append(model.wv[word])
        else:
            word_vec.append(np.zeros(300)) ## used for OOV words
    return word_vec

In [10]:
# tokens = [[tokenize(row[1]),int(row[2])] for row in train_data if tokenize(row[1]) != []]
tokens = np.array(train_data)
train_X = tokens[:,1]
train_Y = tokens[:,[-1]]
# train_X = convert2Vec(model, train_X)
# train_Y = np.array([[y] for y in train_Y])
seq_length = [len(x) for x in train_X]
maxseq_length = max(seq_length)
maxseq_length

158

In [11]:
def zero_padding(maxseq_length, seq):
    zero_pad = np.zeros((maxseq_length) * 300)
    seq_flat = np.reshape(seq, [-1])
    if(len(seq) > maxseq_length):
        zero_pad[0:] = seq_flat[0:maxseq_length * 300]
    else:
        zero_pad[0:len(seq) * 300] = seq_flat
    return zero_pad

# train_X = [zero_padding(maxseq_length, seq) for seq in train_X]
# len(train_X[0])

In [12]:
X = tf.placeholder(tf.float32, shape=[None, maxseq_length * 300])
Y = tf.placeholder(tf.float32, shape=[None, 1])

In [13]:
W = tf.Variable(tf.random_normal([maxseq_length * 300, 1]), name='weight')
b = tf.Variable(tf.random_normal([1]), name='bias')

In [14]:
hypothesis = tf.sigmoid(tf.matmul(X, W) + b)

In [15]:
# cost = -tf.reduce_mean(Y * tf.log(hypothesis) + (1 - Y) *
#                        tf.log(1 - hypothesis))
cost = -tf.reduce_mean(Y * tf.log(hypothesis + 1e-7) + (1 - Y) * tf.log(1 - hypothesis + 1e-7))
# cost_summ = tf.summary.scalar("cost", cost)

In [16]:
train = tf.train.AdamOptimizer(learning_rate=0.001).minimize(cost)

In [ ]:
predicted = tf.cast(hypothesis > 0.5, dtype=tf.float32)
accuracy = tf.reduce_mean(tf.cast(tf.equal(predicted, Y), dtype=tf.float32), name='acc_test')
# acc_summ = tf.summary.scalar("accuracy", accuracy)

In [ ]:
training_epochs = 20
Batch_size = 32
total_batch = int(len(train_X) / Batch_size)
save_path = './saved/model'
saver = tf.train.Saver()

with tf.Session() as sess:
#     merged_summary = tf.summary.merge_all()
#     writer = tf.summary.FileWriter("./logs/logistic")
#     writer.add_graph(sess.graph)  # Show the graph
    
    start_time = time.time()

    # Initialize TensorFlow variables
    sess.run(tf.global_variables_initializer())

    for epoch in range(training_epochs):

        avg_loss = 0
        for step in range(total_batch):
            n = step * Batch_size
            train_batch_X = train_X[n : n + Batch_size]
            train_batch_X = [tokenize(row) for row in train_batch_X]
            train_batch_X = [convert2Vec(model, row) for row in train_batch_X]
            train_batch_X = [zero_padding(maxseq_length, row) for row in train_batch_X]
            train_batch_Y = train_Y[n : n + Batch_size]
            
            cost_val, _ = sess.run([cost, train], feed_dict={X: train_batch_X, Y: train_batch_Y})
            avg_loss += cost_val
            acc = sess.run(accuracy , feed_dict={X: train_batch_X, Y: train_batch_Y})
            print('Batch : ', step + 1, '/', total_batch, '(epoch:', epoch, ')', 
                  ', BCE in this minibatch: ', cost_val, 'accuracy: ', float(acc))

#         summary = sess.run(merged_summary, feed_dict={X: train_X, Y: train_Y})
#         writer.add_summary(summary, global_step=epoch)

#         acc = sess.run(accuracy , feed_dict={X: train_X, Y: train_Y})
        print('epoch:', epoch, ' train_loss:', float(avg_loss/total_batch))
#         print('epoch:', epoch, ' train_loss:', float(avg_loss/total_batch), ' accuracy: ', float(acc))
        saver.save(sess, save_path, epoch)
        
    duration = time.time() - start_time
    minute = int(duration / 60)
    print('learning finish, minutes:', minute)


Batch :  1 / 4687 , BCE in this minibatch:  4.375272 accuracy:  0.53125
Batch :  2 / 4687 , BCE in this minibatch:  5.6948195 accuracy:  0.40625
Batch :  3 / 4687 , BCE in this minibatch:  3.4996824 accuracy:  0.53125
Batch :  4 / 4687 , BCE in this minibatch:  4.1689844 accuracy:  0.4375
Batch :  5 / 4687 , BCE in this minibatch:  2.8030524 accuracy:  0.53125
Batch :  6 / 4687 , BCE in this minibatch:  2.5926893 accuracy:  0.53125
Batch :  7 / 4687 , BCE in this minibatch:  1.5198774 accuracy:  0.71875
Batch :  8 / 4687 , BCE in this minibatch:  4.7177973 accuracy:  0.40625
Batch :  9 / 4687 , BCE in this minibatch:  4.353372 accuracy:  0.5625
Batch :  10 / 4687 , BCE in this minibatch:  4.5040874 accuracy:  0.4375
Batch :  11 / 4687 , BCE in this minibatch:  3.8976686 accuracy:  0.5
Batch :  12 / 4687 , BCE in this minibatch:  3.862039 accuracy:  0.40625
Batch :  13 / 4687 , BCE in this minibatch:  4.092065 accuracy:  0.375
Batch :  14 / 4687 , BCE in this minibatch:  5.0426803 accur

Batch :  114 / 4687 , BCE in this minibatch:  4.536624 accuracy:  0.40625
Batch :  115 / 4687 , BCE in this minibatch:  3.8809793 accuracy:  0.5625
Batch :  116 / 4687 , BCE in this minibatch:  4.1034555 accuracy:  0.4375
Batch :  117 / 4687 , BCE in this minibatch:  4.3019495 accuracy:  0.4375
Batch :  118 / 4687 , BCE in this minibatch:  4.602481 accuracy:  0.375
Batch :  119 / 4687 , BCE in this minibatch:  2.7159438 accuracy:  0.625
Batch :  120 / 4687 , BCE in this minibatch:  3.419805 accuracy:  0.46875
Batch :  121 / 4687 , BCE in this minibatch:  1.3519514 accuracy:  0.71875
Batch :  122 / 4687 , BCE in this minibatch:  5.843424 accuracy:  0.4375
Batch :  123 / 4687 , BCE in this minibatch:  2.457809 accuracy:  0.65625
Batch :  124 / 4687 , BCE in this minibatch:  4.792963 accuracy:  0.46875
Batch :  125 / 4687 , BCE in this minibatch:  5.119233 accuracy:  0.4375
Batch :  126 / 4687 , BCE in this minibatch:  4.02838 accuracy:  0.5
Batch :  127 / 4687 , BCE in this minibatch:  4

Batch :  228 / 4687 , BCE in this minibatch:  3.1861992 accuracy:  0.65625
Batch :  229 / 4687 , BCE in this minibatch:  3.8064559 accuracy:  0.5
Batch :  230 / 4687 , BCE in this minibatch:  2.6129277 accuracy:  0.5
Batch :  231 / 4687 , BCE in this minibatch:  4.1519337 accuracy:  0.4375
Batch :  232 / 4687 , BCE in this minibatch:  4.0449924 accuracy:  0.5
Batch :  233 / 4687 , BCE in this minibatch:  2.5853276 accuracy:  0.59375
Batch :  234 / 4687 , BCE in this minibatch:  4.3809376 accuracy:  0.53125
Batch :  235 / 4687 , BCE in this minibatch:  3.5152562 accuracy:  0.59375
Batch :  236 / 4687 , BCE in this minibatch:  6.6931705 accuracy:  0.28125
Batch :  237 / 4687 , BCE in this minibatch:  2.8811412 accuracy:  0.5
Batch :  238 / 4687 , BCE in this minibatch:  2.5284114 accuracy:  0.59375
Batch :  239 / 4687 , BCE in this minibatch:  5.0552473 accuracy:  0.4375
Batch :  240 / 4687 , BCE in this minibatch:  4.2117796 accuracy:  0.34375
Batch :  241 / 4687 , BCE in this minibatch

Batch :  340 / 4687 , BCE in this minibatch:  4.189187 accuracy:  0.5625
Batch :  341 / 4687 , BCE in this minibatch:  3.043764 accuracy:  0.5625
Batch :  342 / 4687 , BCE in this minibatch:  2.9606447 accuracy:  0.59375
Batch :  343 / 4687 , BCE in this minibatch:  3.9623184 accuracy:  0.46875
Batch :  344 / 4687 , BCE in this minibatch:  2.9080641 accuracy:  0.5625
Batch :  345 / 4687 , BCE in this minibatch:  2.015245 accuracy:  0.75
Batch :  346 / 4687 , BCE in this minibatch:  3.0484824 accuracy:  0.5
Batch :  347 / 4687 , BCE in this minibatch:  4.179044 accuracy:  0.4375
Batch :  348 / 4687 , BCE in this minibatch:  4.203756 accuracy:  0.40625
Batch :  349 / 4687 , BCE in this minibatch:  3.6100473 accuracy:  0.5
Batch :  350 / 4687 , BCE in this minibatch:  3.571753 accuracy:  0.5625
Batch :  351 / 4687 , BCE in this minibatch:  3.9183338 accuracy:  0.53125
Batch :  352 / 4687 , BCE in this minibatch:  4.083475 accuracy:  0.40625
Batch :  353 / 4687 , BCE in this minibatch:  4.

Batch :  453 / 4687 , BCE in this minibatch:  2.0135827 accuracy:  0.625
Batch :  454 / 4687 , BCE in this minibatch:  2.9801211 accuracy:  0.53125
Batch :  455 / 4687 , BCE in this minibatch:  1.6336093 accuracy:  0.71875
Batch :  456 / 4687 , BCE in this minibatch:  4.756543 accuracy:  0.5625
Batch :  457 / 4687 , BCE in this minibatch:  4.3130865 accuracy:  0.5625
Batch :  458 / 4687 , BCE in this minibatch:  2.9109697 accuracy:  0.59375
Batch :  459 / 4687 , BCE in this minibatch:  3.592168 accuracy:  0.53125
Batch :  460 / 4687 , BCE in this minibatch:  3.1023414 accuracy:  0.5625
Batch :  461 / 4687 , BCE in this minibatch:  1.6146325 accuracy:  0.6875
Batch :  462 / 4687 , BCE in this minibatch:  2.596423 accuracy:  0.53125
Batch :  463 / 4687 , BCE in this minibatch:  2.1770449 accuracy:  0.53125
Batch :  464 / 4687 , BCE in this minibatch:  3.0491052 accuracy:  0.46875
Batch :  465 / 4687 , BCE in this minibatch:  2.5889583 accuracy:  0.59375
Batch :  466 / 4687 , BCE in this 

...

Batch :  1911 / 4687 , BCE in this minibatch:  0.29338032 accuracy:  0.875
Batch :  1912 / 4687 , BCE in this minibatch:  0.26597774 accuracy:  0.84375
Batch :  1913 / 4687 , BCE in this minibatch:  0.41401517 accuracy:  0.875
Batch :  1914 / 4687 , BCE in this minibatch:  0.51614827 accuracy:  0.6875
Batch :  1915 / 4687 , BCE in this minibatch:  0.3113541 accuracy:  0.84375
Batch :  1916 / 4687 , BCE in this minibatch:  0.40755686 accuracy:  0.84375
Batch :  1917 / 4687 , BCE in this minibatch:  0.53854465 accuracy:  0.84375
Batch :  1918 / 4687 , BCE in this minibatch:  1.0816851 accuracy:  0.6875
Batch :  1919 / 4687 , BCE in this minibatch:  0.3360526 accuracy:  0.8125
Batch :  1920 / 4687 , BCE in this minibatch:  0.37261534 accuracy:  0.8125
Batch :  1921 / 4687 , BCE in this minibatch:  0.36716276 accuracy:  0.75
Batch :  1922 / 4687 , BCE in this minibatch:  0.16456972 accuracy:  0.90625
Batch :  1923 / 4687 , BCE in this minibatch:  0.2850877 accuracy:  0.875
Batch :  1924 / 

Batch :  2023 / 4687 , BCE in this minibatch:  0.23738047 accuracy:  0.90625
Batch :  2024 / 4687 , BCE in this minibatch:  0.1896388 accuracy:  0.90625
Batch :  2025 / 4687 , BCE in this minibatch:  0.34288973 accuracy:  0.875
Batch :  2026 / 4687 , BCE in this minibatch:  0.5268542 accuracy:  0.6875
Batch :  2027 / 4687 , BCE in this minibatch:  0.3399124 accuracy:  0.8125
Batch :  2028 / 4687 , BCE in this minibatch:  0.2575403 accuracy:  0.9375
Batch :  2029 / 4687 , BCE in this minibatch:  0.3860278 accuracy:  0.875
Batch :  2030 / 4687 , BCE in this minibatch:  0.34217307 accuracy:  0.84375
Batch :  2031 / 4687 , BCE in this minibatch:  0.32851022 accuracy:  0.8125
Batch :  2032 / 4687 , BCE in this minibatch:  0.49360883 accuracy:  0.78125
Batch :  2033 / 4687 , BCE in this minibatch:  0.27097917 accuracy:  0.875
Batch :  2034 / 4687 , BCE in this minibatch:  0.9932209 accuracy:  0.75
Batch :  2035 / 4687 , BCE in this minibatch:  0.1887622 accuracy:  0.9375
Batch :  2036 / 4687

Batch :  2135 / 4687 , BCE in this minibatch:  0.3916043 accuracy:  0.84375
Batch :  2136 / 4687 , BCE in this minibatch:  0.6117258 accuracy:  0.8125
Batch :  2137 / 4687 , BCE in this minibatch:  0.51623774 accuracy:  0.71875
Batch :  2138 / 4687 , BCE in this minibatch:  0.647426 accuracy:  0.90625
Batch :  2139 / 4687 , BCE in this minibatch:  0.26626387 accuracy:  0.90625
Batch :  2140 / 4687 , BCE in this minibatch:  0.41541308 accuracy:  0.8125
Batch :  2141 / 4687 , BCE in this minibatch:  0.38022268 accuracy:  0.8125
Batch :  2142 / 4687 , BCE in this minibatch:  0.4121387 accuracy:  0.78125
Batch :  2143 / 4687 , BCE in this minibatch:  0.16979499 accuracy:  0.9375
Batch :  2144 / 4687 , BCE in this minibatch:  0.30167866 accuracy:  0.875
Batch :  2145 / 4687 , BCE in this minibatch:  0.46848327 accuracy:  0.84375
Batch :  2146 / 4687 , BCE in this minibatch:  0.3795774 accuracy:  0.8125
Batch :  2147 / 4687 , BCE in this minibatch:  0.4443214 accuracy:  0.90625
Batch :  2148

Batch :  2244 / 4687 , BCE in this minibatch:  0.42283612 accuracy:  0.84375
Batch :  2245 / 4687 , BCE in this minibatch:  0.21290892 accuracy:  0.9375
Batch :  2246 / 4687 , BCE in this minibatch:  0.15759447 accuracy:  0.96875
Batch :  2247 / 4687 , BCE in this minibatch:  0.1989219 accuracy:  0.9375
Batch :  2248 / 4687 , BCE in this minibatch:  0.6303096 accuracy:  0.84375
Batch :  2249 / 4687 , BCE in this minibatch:  0.22848989 accuracy:  0.9375
Batch :  2250 / 4687 , BCE in this minibatch:  0.48255128 accuracy:  0.84375
Batch :  2251 / 4687 , BCE in this minibatch:  0.5475377 accuracy:  0.8125
Batch :  2252 / 4687 , BCE in this minibatch:  0.25368136 accuracy:  0.90625
Batch :  2253 / 4687 , BCE in this minibatch:  0.30030048 accuracy:  0.84375
Batch :  2254 / 4687 , BCE in this minibatch:  0.36010003 accuracy:  0.84375
Batch :  2255 / 4687 , BCE in this minibatch:  0.3477885 accuracy:  0.84375
Batch :  2256 / 4687 , BCE in this minibatch:  0.23562318 accuracy:  0.90625
Batch :

Batch :  2355 / 4687 , BCE in this minibatch:  0.57574636 accuracy:  0.875
Batch :  2356 / 4687 , BCE in this minibatch:  0.35193753 accuracy:  0.90625
Batch :  2357 / 4687 , BCE in this minibatch:  0.21086769 accuracy:  0.9375
Batch :  2358 / 4687 , BCE in this minibatch:  0.84911495 accuracy:  0.84375
Batch :  2359 / 4687 , BCE in this minibatch:  0.37968123 accuracy:  0.8125
Batch :  2360 / 4687 , BCE in this minibatch:  0.4977408 accuracy:  0.8125
Batch :  2361 / 4687 , BCE in this minibatch:  0.47077045 accuracy:  0.875
Batch :  2362 / 4687 , BCE in this minibatch:  0.26610345 accuracy:  0.84375
Batch :  2363 / 4687 , BCE in this minibatch:  0.34920916 accuracy:  0.9375
Batch :  2364 / 4687 , BCE in this minibatch:  0.51702857 accuracy:  0.8125
Batch :  2365 / 4687 , BCE in this minibatch:  0.49763143 accuracy:  0.6875
Batch :  2366 / 4687 , BCE in this minibatch:  0.19141966 accuracy:  0.9375
Batch :  2367 / 4687 , BCE in this minibatch:  0.80253977 accuracy:  0.625
Batch :  2368